In [ ]:
import os
import zipfile
import requests
import jsonlines
from tqdm import tqdm
from pathlib import Path
from pycocotools.coco import COCO
from pycocotools import mask as maskUtils

# Download Annotations

In [ ]:
url = 'http://images.cocodataset.org/annotations/'
file = 'stuff_annotations_trainval2017.zip'
if not Path(f'./{file}').exists():
    response = requests.get(url + file)
    with open(file, 'wb') as f:
        f.write(response.content)

    with zipfile.ZipFile(file, 'r') as zipf:
        zipf.extractall(Path())

# for split in ['train', 'val']:
#     file = f'./annotations/stuff_{split}2017_pixelmaps'
#     if not Path(file).exists():
#         with zipfile.ZipFile(file + '.zip', 'r') as zipf:
#             zipf.extractall(Path('./annotations'))


# Stuff Segmentation Task

In [ ]:
train_data = COCO('annotations/stuff_train2017.json')
val_data = COCO('annotations/stuff_val2017.json')

In [ ]:
for split, data in zip(['train', 'validation'], [train_data, val_data]):
    with jsonlines.open(f'data/stuff_{split}.jsonl', mode='w') as writer:
        for image_id, image_info in tqdm(data.imgs.items()):
            categories, sem_rles = [], []
            anns = data.imgToAnns[image_id]
            file_name = image_info['file_name']
            height, width = image_info['height'], image_info['width']
            for ann in anns:
                categories.append(ann['category_id'] - 92)
                segm = ann['segmentation']
                if isinstance(segm, list):
                    rles = maskUtils.frPyObjects(segm, height, width)
                    rle = maskUtils.merge(rles)
                    rle['counts'] = rle['counts'].decode()
                elif isinstance(segm['counts'], list):
                    rle = maskUtils.frPyObjects(segm, height, width)
                else:
                    rle = segm
                sem_rles.append(rle)
            writer.write({
                'image': file_name, 'categories': categories, 'sem.rles': sem_rles
            })

In [ ]:
for split in ['train', 'validation']:
    file_path = f'data/stuff_{split}.jsonl'
    with zipfile.ZipFile(f'data/stuff_{split}.zip', 'w', zipfile.ZIP_DEFLATED) as zipf:
        zipf.write(file_path, os.path.basename(file_path))